In [1]:
from pymongo import MongoClient

# Verbinde zur Datenbank
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
collection = db["genius"]
sample_collection = db["sampled_songs"]

# 100.000 zufällige Songs ziehen
sampled_songs = list(collection.aggregate([{"$sample": {"size": 10000}}]))

# In neue Collection einfügen
sample_collection.insert_many(sampled_songs)

print("100.000 zufällige Songs erfolgreich kopiert.")


100.000 zufällige Songs erfolgreich kopiert.


In [2]:
from pymongo import MongoClient

client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
sample_collection = db["sampled_songs"]

# Aggregation: Gruppiere nach Sprache und zähle
language_stats = list(sample_collection.aggregate([
    {"$match": {"language": {"$exists": True, "$ne": None}}},
    {"$group": {
        "_id": "$language",
        "count": {"$sum": 1}
    }},
    {"$sort": {"count": -1}}  # Sortiere nach Häufigkeit
]))

# Ausgabe
for entry in language_stats:
    print(f"Sprache: {entry['_id']}, Anzahl: {entry['count']}")


Sprache: en, Anzahl: 6661
Sprache: es, Anzahl: 478
Sprache: fr, Anzahl: 413
Sprache: ru, Anzahl: 335
Sprache: de, Anzahl: 311
Sprache: pt, Anzahl: 290
Sprache: it, Anzahl: 221
Sprache: pl, Anzahl: 182
Sprache: ko, Anzahl: 82
Sprache: tr, Anzahl: 82
Sprache: sv, Anzahl: 65
Sprache: ja, Anzahl: 61
Sprache: nl, Anzahl: 51
Sprache: fi, Anzahl: 48
Sprache: he, Anzahl: 31
Sprache: da, Anzahl: 31
Sprache: el, Anzahl: 29
Sprache: zh, Anzahl: 24
Sprache: ar, Anzahl: 21
Sprache: ro, Anzahl: 18
Sprache: vi, Anzahl: 16
Sprache: no, Anzahl: 14
Sprache: cs, Anzahl: 14
Sprache: lv, Anzahl: 13
Sprache: sk, Anzahl: 12
Sprache: fil, Anzahl: 10
Sprache: fa, Anzahl: 10
Sprache: hu, Anzahl: 9
Sprache: az, Anzahl: 6
Sprache: id, Anzahl: 4
Sprache: is, Anzahl: 3
Sprache: ca, Anzahl: 3
Sprache: af, Anzahl: 3
Sprache: bg, Anzahl: 2
Sprache: sq, Anzahl: 2
Sprache: ne, Anzahl: 2
Sprache: mk, Anzahl: 2
Sprache: hi, Anzahl: 2
Sprache: eu, Anzahl: 2
Sprache: et, Anzahl: 2
Sprache: lt, Anzahl: 1
Sprache: sr, Anzahl:

In [3]:
from pymongo import MongoClient
import random

# Verbindung zur MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
collection = db["genius"]           # Originaldaten
filtered_collection = db["subset"]  # Neue Collection

# Zielsprachen
target_languages = ["en", "de", "es", "fr", "it"]

# Optional: vorher leeren
filtered_collection.delete_many({})

# MONGO AGGREGATION: Zufällig 100.000 Songs mit Sprache in den gewünschten
pipeline = [
    {"$match": {"language": {"$in": target_languages}}}
]

results = list(collection.aggregate(pipeline))

# In neue Collection speichern
if results:
    filtered_collection.insert_many(results)

print(f"{len(results)} Songs wurden extrahiert und in 'subset' gespeichert.")


4117991 Songs wurden extrahiert und in 'subset' gespeichert.


In [4]:
from pymongo import MongoClient

client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
subset = db["subset"]
sampled = db["sampled_subset"]

# Ziehe 100.000 zufällige Songs
pipeline = [
    {"$sample": {"size": 100000}}
]

results = list(subset.aggregate(pipeline))

# In neue Collection einfügen
if results:
    sampled.insert_many(results)

print(f"{len(results)} Songs wurden zufällig aus 'subset' gezogen und in 'sampled_subset' gespeichert.")


100000 Songs wurden zufällig aus 'subset' gezogen und in 'sampled_subset' gespeichert.


In [7]:
from pymongo import MongoClient

client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
sampled = db["sampled_subset"]

# Aggregation: Zähle die Anzahl der Songs pro Genre
pipeline = [
    {"$match": {"tag": {"$exists": True, "$ne": None}}},
    {"$group": {"_id": "$tag", "count": {"$sum": 1}}},
    {"$sort": {"count": -1}}
]

results = list(sampled.aggregate(pipeline))

# Ausgabe
for genre in results:
    print(f"{genre['_id']}: {genre['count']}")


rap: 35633
pop: 34561
rock: 15728
misc: 8072
rb: 3992
country: 2014


In [8]:
from pymongo import MongoClient
import re

client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
collection = db["sampled_subset"]  # oder dein gewünschter Collection-Name

# Alle Artists, deren Name "Genius" irgendwo enthält (case-insensitive)
cursor = collection.find({
    "artist": {
        "$regex": re.compile("genius", re.IGNORECASE)
    }
}, {"_id": 0, "artist": 1}).distinct("artist")

# Ausgabe
for artist in cursor:
    print(artist)


7xvethegenius
AGenius
AcEtheGeniusOfficial
Christian Genius
Comedy Genius
Country Genius
Deont Genius
Eugenius (band)
Fashion Genius
Game Genius
Genius
Genius  (Chinese Translations)
Genius Brasil Tradues
Genius Community
Genius Danmark
Genius Deutsche bersetzungen
Genius Deutschland
Genius Dream Album
Genius Editors
Genius English Translations
Genius France
Genius France [Archives]
Genius Korea
Genius Lists
Genius Romanizations
Genius Russian Translations ( )
Genius South Africa Translations
Genius South Asia
Genius Traducciones al Espaol
Genius Traductions Franaises
Genius Traduzioni Italiane
Genius Translations
Genius UK
Genius Users
Genius sterreich
Genius111
Graffiti Genius
Hoshi (Genius Contributor)
Lit Genius
MEDIA ARTS GENIUSES (MAG)
Math Genius
News Genius
News Genius Deutschland
Ningenius
Noble da genius
Original West End Cast of Eugenius
Outside the Lines With Rap Genius
Perfume Genius
Phantom Genius
Polskie tumaczenia Genius
Rap Genius
Rap Genius Deutschland
Rap Genius Edit

In [ ]:
from pymongo import MongoClient

# Verbindung zur MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
collection = db["sampled_subset"]

# Liste der Genius-"Künstler", die entfernt werden sollen
unwanted_artists = [
    "Charles Dickens",
    "Genius Traductions Franaises",
    "Leo Tolstoy",
    "Edith Wharton",
    "Mr. Allen",
    "Abraham Lincoln",
    "Mark Twain",
    "Friedrich Schiller",
    "Emily Dickinson",
    "James Fenimore Cooper",
    "George Eliot",
    "The Supreme Court of the United States",
    "Alexandre Dumas, Pre",
    "La Bible de Jrusalem",
    "Thomas Hardy",
    "Willie Nelson",
    "Joseph Conrad",
    "Seinfeld",
    "Henry James",
    "Noam Chomsky",
    "D. H. Lawrence",
    "Chief Keef",
    "Richard F. Burton",
    "Frank Zappa",
    "Charlotte Bront",
    "Walt Whitman",
    "Karl Marx",
    "The SCP Foundation",
    "Johann Wolfgang von Goethe",
    "Herman Melville",
    "Christina Rossetti",
    "Friedrich Nietzsche",
    "William Makepeace Thackeray",
    "Sir Thomas Malory",
    "K-Rino",
    "Charles Chesnutt",
    "Ben Jonson",
    "URLtv",
    "Barack Obama",
    "Fyodor Dostoevsky",
    "W.E.B. Du Bois",
    "Nathaniel Hawthorne",
    "YOUNG DIAMOND",
    "Jules Verne",
    "Lord Byron",
    "Alexander Hamilton, John Jay, James Madison",
    "Brothers Grimm",
    "Mina",
    "Molire",
    "Ralph Waldo Emerson"
]

# Schritt 1: Entfernen der Songs mit diesen Künstlern
delete_result = collection.delete_many({"artist": {"$in": unwanted_artists}})
print(f"{delete_result.deleted_count} Songs wurden mit unerwünschten 'Genius'-Künstlern entfernt.")

# Schritt 2: Zählen der verbleibenden Songs
remaining_count = collection.count_documents({})
print(f"{remaining_count} Songs sind noch in der 'sampled_subset'-Collection übrig.")


124 Songs wurden mit unerwünschten 'Genius'-Künstlern entfernt.
99260 Songs sind noch in der 'sampled_subset'-Collection übrig.


In [11]:
from pymongo import MongoClient

# Verbindung zur MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
collection = db["sampled_subset"]

# Aggregation: Zähle die Anzahl der Songs pro Artist
pipeline = [
    {"$match": {"artist": {"$exists": True, "$ne": None}}},  # Filtert Songs ohne Artist
    {"$group": {"_id": "$artist", "count": {"$sum": 1}}},   # Gruppiert nach Artist und zählt
    {"$sort": {"count": -1}}  # Sortiert nach Häufigkeit (absteigend)
]

results = list(collection.aggregate(pipeline))

# Ausgabe der Künstler und ihrer Häufigkeit
for artist in results:
    print(f"{artist['_id']}: {artist['count']}")


Charles Dickens: 286
Genius Traductions Franaises: 124
  (Leo Tolstoy): 97
Edith Wharton: 92
Mr. Allen: 80
Abraham Lincoln: 78
Mark Twain: 68
William Shakespeare: 54
Lil Wayne: 54
Friedrich Schiller: 53
Emily Dickinson: 52
James Fenimore Cooper: 48
George Eliot: 48
The Supreme Court of the United States: 46
Alexandre Dumas, Pre: 46
Lil B: 46
Gucci Mane: 45
La Bible de Jrusalem: 44
Thomas Hardy: 44
Willie Nelson: 44
Joseph Conrad: 43
2Pac: 43
Seinfeld: 42
Henry James: 41
Noam Chomsky: 40
D. H. Lawrence: 40
Chief Keef: 40
Richard F. Burton: 39
Frank Zappa: 38
JuL: 38
Holy Bible (KJV): 38
Charlotte Bront: 37
Walt Whitman: 36
Karl Marx: 35
The SCP Foundation: 34
Chris Brown: 34
Johann Wolfgang von Goethe: 34
E-40: 34
Herman Melville: 34
Christina Rossetti: 33
Friedrich Nietzsche: 33
William Makepeace Thackeray: 33
KIDZ BOP Kids: 32
Juice WRLD: 32
Jane Austen: 31
Killah Priest: 31
Dr. Fassi: 30
Royce da 5'9": 29
David Hume: 28
John Calvin: 28
Francois Rabelais: 28
Anthony Trollope: 28
Victo

In [13]:
from pymongo import MongoClient

# Verbindung zur MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
collection = db["sampled_subset"]

# Liste der nicht-musikalischen "Künstler", die entfernt werden sollen
unwanted_artists = [
    "Charles Dickens",
    "Leo Tolstoy",
    "Edith Wharton",
    "Mr. Allen",
    "Abraham Lincoln",
    "Mark Twain",
    "Friedrich Schiller",
    "Emily Dickinson",
    "James Fenimore Cooper",
    "George Eliot",
    "The Supreme Court of the United States",
    "Alexandre Dumas, Pre",
    "La Bible de Jrusalem",
    "Thomas Hardy",
    "Willie Nelson",
    "Joseph Conrad",
    "Seinfeld",
    "Henry James",
    "Noam Chomsky",
    "D. H. Lawrence",
    "Chief Keef",
    "Richard F. Burton",
    "Frank Zappa",
    "Charlotte Bront",
    "Walt Whitman",
    "Karl Marx",
    "The SCP Foundation",
    "Johann Wolfgang von Goethe",
    "Herman Melville",
    "Christina Rossetti",
    "Friedrich Nietzsche",
    "William Makepeace Thackeray",
    "Sir Thomas Malory",
    "K-Rino",
    "Charles Chesnutt",
    "Ben Jonson",
    "URLtv",
    "Barack Obama",
    "Fyodor Dostoevsky",
    "W.E.B. Du Bois",
    "Nathaniel Hawthorne",
    "YOUNG DIAMOND",
    "Jules Verne",
    "Lord Byron",
    "Alexander Hamilton, John Jay, James Madison",
    "Brothers Grimm",
    "Mina",
    "Molire",
    "Ralph Waldo Emerson"
]

# Schritt 1: Entfernen der Songs mit diesen Künstlern
delete_result = collection.delete_many({"artist": {"$in": unwanted_artists}})
print(f"{delete_result.deleted_count} Songs wurden mit unerwünschten Künstlern entfernt.")

# Schritt 2: Zählen der verbleibenden Songs
remaining_count = collection.count_documents({})
print(f"{remaining_count} Songs sind noch in der 'sampled_subset'-Collection übrig.")


2063 Songs wurden mit unerwünschten Künstlern entfernt.
97197 Songs sind noch in der 'sampled_subset'-Collection übrig.


In [14]:
from pymongo import MongoClient

# Verbindung zur MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
collection = db["sampled_subset"]

# Liste der eindeutig nicht-musikalischen Personen / Quellen
unwanted_artists = [
    "William Hazlitt",
    "Jack London",
    "Anton Chekhov",
    "Homer",
    "Anne Bront",
    "Virginia Woolf",
    "Elizabeth Gaskell",
    "Jasmine Mulliken",
    "Robert William Service",
    "Ford Madox Ford",
    "Georg Wilhelm Friedrich Hegel",
    "Robert Burns",
    "Sgrindle",  # unklar, wahrscheinlich kein Musiker
    "Mario William Vitale",
    "Giovanni Boccaccio",
    "Henry Fielding",
    "Anne Sexton",
    "Aristotle",
    "Nikolai Gogol",
    "Gustave Flaubert",
    "Dr. Jessica Stock",
    "Laurence Overmire",
    "Sir Arthur Conan Doyle",
    "Theodor Fontane",
    "Icelandic Saga",
    "Grey's Anatomy",
    "Immanuel Kant",
    "G. R. S. Mead",
    "William Butler Yeats",
    "Edgar Rice Burroughs",
    "Thomas Hobbes",
    "John Milton",
    "Paul Shapera",
    "Rabindranath Tagore",
    "William Wordsworth",
    "Howard Zinn",
    "George Bernard Shaw",
    "TransPacific Partnership (TPP) Negotiating Parties"
]

# Songs mit diesen Künstlern aus der Collection entfernen
delete_result = collection.delete_many({"artist": {"$in": unwanted_artists}})
print(f"{delete_result.deleted_count} Songs wurden mit nicht-musikalischen Künstlern entfernt.")

# Verbleibende Songs zählen
remaining_count = collection.count_documents({})
print(f"{remaining_count} Songs sind noch in der 'sampled_subset'-Collection übrig.")


548 Songs wurden mit nicht-musikalischen Künstlern entfernt.
96649 Songs sind noch in der 'sampled_subset'-Collection übrig.


In [15]:
from pymongo import MongoClient

# Verbindung zur MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
collection = db["sampled_subset"]

# Liste der nicht-musikalischen Quellen / Personen aus deinem zweiten Batch
unwanted_artists = [
    "TransPacific Partnership (TPP) Negotiating Parties",
    "Plutarch",
    "George Orwell",
    "Unknown Artist",
    "Unknown Author",
    "Alice Sebold",
    "John Steinbeck",
    "George Meredith",
    "Dante Alighieri",
    "Robert Louis Stevenson",
    "Laurence Sterne",
    "James Joyce",
    "Miguel de Cervantes Saavedra",
    "Mary Shelley",
    "Geoffrey Chaucer",
    "Solomon Northup",
    "Petrarch",
    "Dominic Riccitello",
    "Sigmund Freud",
    "Malcolm X",
    "Samuel Taylor Coleridge",
    "Heinrich Heine",
    "St. Thomas Aquinas",
    "Michel de Montaigne",
    "Alfred Lord Tennyson",
    "Bram Stoker",
    "Regular Show",  # TV-Serie
    "Coran",  # religiöser Text
    "Alexis de Tocqueville",
    "Christopher Marlowe",
    "Henrik Ibsen",
    "Lady Augusta Gregory",
    "Ambrose Bierce",
    "Blaise Pascal",
    "Henry David Thoreau"
]

# Songs mit diesen Künstlern löschen
delete_result = collection.delete_many({"artist": {"$in": unwanted_artists}})
print(f"{delete_result.deleted_count} Songs wurden mit nicht-musikalischen Künstlern entfernt.")

# Verbleibende Songs zählen
remaining_count = collection.count_documents({})
print(f"{remaining_count} Songs sind noch in der 'sampled_subset'-Collection übrig.")


344 Songs wurden mit nicht-musikalischen Künstlern entfernt.
96305 Songs sind noch in der 'sampled_subset'-Collection übrig.


In [16]:
from pymongo import MongoClient

# Verbindung zur MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
collection = db["sampled_subset"]

# Liste nicht-musikalischer Einträge aus deiner großen Liste
unwanted_artists = [
    "Donald Trump",
    "Avatar: The Last Airbender",
    "Masterworks of Brit Lit",
    "Dr. L. Craig",
    "William H. Babcock",
    "Guillaume Apollinaire",
    "Joseph Smith, Jr.",
    "Kenneth W. Starr",
    "Home Runs of the Day",
    "Jonathan Swift",
    "Saint Augustine",
    "Margaret Fuller",
    "John Stuart Mill",
    "Epictetus",
    "Joseph Fort Newton",
    "Alan Watts",
    "W. H. Auden",
    "Friedrich Engels",
    "Harriet Beecher Stowe",
    "Robert Frost",
    "John Ruskin",
    "Benedict De Spinoza",
    "Friends (TV)",
    "Albert Camus",
    "HilburnEnglish",
    "Mary Libertin",
]

# Löschen dieser Einträge
delete_result = collection.delete_many({"artist": {"$in": unwanted_artists}})
print(f"{delete_result.deleted_count} nicht-musikalische Einträge wurden entfernt.")

# Noch vorhandene Dokumente zählen
remaining = collection.count_documents({})
print(f"{remaining} musikalische Einträge verbleiben in der 'sampled_subset'-Collection.")


195 nicht-musikalische Einträge wurden entfernt.
96110 musikalische Einträge verbleiben in der 'sampled_subset'-Collection.


In [38]:
from pymongo import MongoClient
from collections import Counter, defaultdict
import nltk
import re

# Stopwords vorbereiten
nltk.download('stopwords')
from nltk.corpus import stopwords

# Sprachen und ihre Stoppwörter
supported_langs = {
    "en": stopwords.words("english"),
    "de": stopwords.words("german"),
    "es": stopwords.words("spanish"),
    "fr": stopwords.words("french"),
    "it": stopwords.words("italian"),
}

# Strukturmarkierungen, die ignoriert werden sollen
section_markers = {
    "verse", "chorus", "hook", "bridge", "intro", "outro", "refrain",
    "pre-chorus", "interlude", "instrumental", "drop", "solo", "post-chorus"
}

# Verbindung zur MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
collection = db["sampled_subset"]
output_collection = db["top_words_by_artist_real"]

# Datenstrukturen vorbereiten
artist_word_counts = defaultdict(Counter)
artist_tags = defaultdict(Counter)

# Alle Songs im Datensatz holen
songs = collection.find()

for song in songs:
    artist = str(song.get("artist", "")).strip()
    lyrics = song.get("lyrics", "")
    lang = song.get("language", "en")
    tag = song.get("tag", "").lower()
    year = song.get("year", None)
    views = song.get("views", 0)

    if not artist or not lyrics or lang not in supported_langs:
        continue

    # Tag zählen
    if tag:
        artist_tags[artist][tag] += 1

    # Lyrics bereinigen und filtern
    words = re.findall(r'\b\w+\b', lyrics.lower())
    filtered = [
        word for word in words
        if word not in supported_langs[lang]
        and word not in section_markers
        and len(word) > 2
    ]

    artist_word_counts[artist].update(filtered)

# Ergebnisse speichern
output_collection.delete_many({})
for artist, counter in artist_word_counts.items():
    top_words = counter.most_common(10)
    most_common_tag = artist_tags[artist].most_common(1)
    tag = most_common_tag[0][0] if most_common_tag else "unknown"

    output_collection.insert_one({
        "artist": artist,
        "tag": tag,
        "top_words": top_words,
        "year": year,
        "views": views
    })

print("Top-Wörter + Genres wurden für alle Artists gespeichert.")


[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/detjonbibai/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Top-Wörter + Genres wurden für alle Artists gespeichert.


In [ ]:
from pymongo import MongoClient
from textblob import TextBlob
from googletrans import Translator
import re

# Verbindung zur MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
collection = db["sampled_subset"]
output_collection = db["song_sentiment_analysis"]

translator = Translator()

# Songs laden
songs = collection.find({
    "lyrics": {"$exists": True, "$ne": None},
    "language": {"$in": ["en", "de", "es", "fr", "it"]},
    "artist": {"$exists": True},
    "tag": {"$exists": True},
    "year": {"$exists": True},
    "views": {"$exists": True}
})

output_collection.delete_many({})  # Bestehende Einträge löschen

for song in songs:
    lyrics = song.get("lyrics", "")
    language = song.get("language", "en")
    artist = str(song.get("artist", "")).strip()
    tag = str(song.get("tag", "unknown")).lower()
    year = song.get("year", None)
    views = song.get("views", 0)

    if not lyrics or not artist or not language:
        continue

    try:
        # Wenn die Sprache nicht Englisch ist, übersetzen
        if language != "en":
            translated = translator.translate(lyrics, src=language, dest="en")
            text = translated.text
        else:
            text = lyrics

        # Sentiment Score berechnen
        blob = TextBlob(text)
        polarity = round(blob.sentiment.polarity, 4)  # -1 = negativ, +1 = positiv

        output_collection.insert_one({
            "artist": artist,
            "tag": tag,
            "language": language,
            "year": year,
            "views": views,
            "sentiment_score": polarity
        })

    except Exception as e:
        print(f"Fehler bei Song von {artist}: {e}")
        continue

print("✅ Sentimentanalyse abgeschlossen und gespeichert.")


In [58]:
from textblob import TextBlob
from googletrans import Translator

# Benutzer gibt Sprache und Text ein
language = input("Welche Sprache hat dein Text? (en, de, es, fr, it): ").strip().lower()
text = input("Gib den Liedtext oder beliebigen Text ein:\n")

translator = Translator()

# Text ggf. ins Englische übersetzen
if language != "en":
    try:
        translated = translator.translate(text, src=language, dest="en")
        print(f"\nÜbersetzt ins Englische:\n{translated.text}")
        text_en = translated.text
    except Exception as e:
        print(f"Fehler bei Übersetzung: {e}")
        text_en = text  # Fallback: Originaltext verwenden
else:
    text_en = text

# Sentiment analysieren
blob = TextBlob(text_en)
polarity = round(blob.sentiment.polarity, 4)  # -1 (negativ) bis +1 (positiv)
subjectivity = round(blob.sentiment.subjectivity, 4)  # 0 (objektiv) bis 1 (subjektiv)

# Ergebnis anzeigen
print("\n🎯 Sentimentanalyse:")
print(f"Stimmung (Polarity): {polarity}  -> {'Positiv' if polarity > 0 else 'Negativ' if polarity < 0 else 'Neutral'}")
print(f"Subjektivität: {subjectivity}")



Übersetzt ins Englische:
I hate school my day was miserable

🎯 Sentimentanalyse:
Stimmung (Polarity): -0.9  -> Negativ
Subjektivität: 0.95


In [36]:
from pymongo import MongoClient

# Verbindung zur MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
source_collection = db["sampled_subset"]

# Ziel-Sprachen (du kannst die Liste bei Bedarf erweitern)
languages = ["en", "de", "es", "fr", "it"]

for lang in languages:
    # Neue Collection pro Sprache vorbereiten
    target_collection = db[f"sampled_subset_{lang}"]
    target_collection.delete_many({})  # Vorherige Inhalte löschen (optional)

    # Dokumente mit passender Sprache abrufen
    docs = source_collection.find({"language": lang})

    # In die entsprechende Collection einfügen
    if docs:
        target_collection.insert_many(docs)

    print(f"✅ Sprache '{lang}' erfolgreich in 'sampled_subset_{lang}' gespeichert.")

print("🎉 Alle Sprach-Collections wurden erstellt.")


✅ Sprache 'en' erfolgreich in 'sampled_subset_en' gespeichert.
✅ Sprache 'de' erfolgreich in 'sampled_subset_de' gespeichert.
✅ Sprache 'es' erfolgreich in 'sampled_subset_es' gespeichert.
✅ Sprache 'fr' erfolgreich in 'sampled_subset_fr' gespeichert.
✅ Sprache 'it' erfolgreich in 'sampled_subset_it' gespeichert.
🎉 Alle Sprach-Collections wurden erstellt.


In [ ]:
from pymongo import MongoClient
from textblob import TextBlob
from googletrans import Translator
import re

# Verbindung zur MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
collection = db["sampled_subset_de"]
output_collection = db["song_sentiment_analysis_de"]

translator = Translator()


# Songs laden
songs = collection.find({
    "lyrics": {"$exists": True, "$ne": None},
    "language": {"$in": ["en", "de", "es", "fr", "it"]},
    "artist": {"$exists": True},
    "tag": {"$exists": True},
    "year": {"$exists": True},
    "views": {"$exists": True}
})

output_collection.delete_many({})  # Bestehende Einträge löschen

for song in songs:
    lyrics = song.get("lyrics", "")
    language = song.get("language", "en")
    artist = str(song.get("artist", "")).strip()
    tag = str(song.get("tag", "unknown")).lower()
    year = song.get("year", None)
    views = song.get("views", 0)
    title = song.get("title", "unknown")

    if not lyrics or not artist or not language:
        continue

    try:
        # Wenn die Sprache nicht Englisch ist, übersetzen
        if language != "en":
            translated = translator.translate(lyrics, src=language, dest="en")
            text = translated.text
        else:
            text = lyrics

        # Sentiment Score berechnen
        blob = TextBlob(text)
        polarity = round(blob.sentiment.polarity, 4)  # -1 = negativ, +1 = positiv

        output_collection.insert_one({
            "artist": artist,
            "tag": tag,
            "language": language,
            "year": year,
            "views": views,
            "sentiment_score": polarity,
            "title": title,
        })

    except Exception as e:
        print(f"Fehler bei Song von {artist}: {e}")
        continue

print("✅ Sentimentanalyse für Songs abgeschlossen und gespeichert.")


Fehler bei Song von matza: the JSON object must be str, bytes or bytearray, not NoneType
Fehler bei Song von Paul Johann Anselm Ritter von Feuerbach: the JSON object must be str, bytes or bytearray, not NoneType
Fehler bei Song von Ulrich Plenzdorf: the JSON object must be str, bytes or bytearray, not NoneType
Fehler bei Song von Eins Zwo: the JSON object must be str, bytes or bytearray, not NoneType
Fehler bei Song von 3Plusss: The read operation timed out
Fehler bei Song von Annette von Droste-Hlshoff: sequence item 0: expected str instance, NoneType found
Fehler bei Song von Alexa Feser & Kool Savas: The read operation timed out
Fehler bei Song von AchtVier: the JSON object must be str, bytes or bytearray, not NoneType
Fehler bei Song von Paul Johann Anselm Ritter von Feuerbach: the JSON object must be str, bytes or bytearray, not NoneType
Fehler bei Song von Christoph May: the JSON object must be str, bytes or bytearray, not NoneType
Fehler bei Song von Samy Deluxe: the JSON object

In [39]:
from pymongo import MongoClient
from textblob import TextBlob
from googletrans import Translator
import re

# Verbindung zur MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
collection = db["sampled_subset_it"]
output_collection = db["song_sentiment_analysis_it"]

translator = Translator()


# Songs laden
songs = collection.find({
    "lyrics": {"$exists": True, "$ne": None},
    "language": {"$in": ["en", "de", "es", "fr", "it"]},
    "artist": {"$exists": True},
    "tag": {"$exists": True},
    "year": {"$exists": True},
    "views": {"$exists": True}
})

output_collection.delete_many({})  # Bestehende Einträge löschen

for song in songs:
    lyrics = song.get("lyrics", "")
    language = song.get("language", "en")
    artist = str(song.get("artist", "")).strip()
    tag = str(song.get("tag", "unknown")).lower()
    year = song.get("year", None)
    views = song.get("views", 0)
    title = song.get("title", "unknown")

    if not lyrics or not artist or not language:
        continue

    try:
        # Wenn die Sprache nicht Englisch ist, übersetzen
        if language != "en":
            translated = translator.translate(lyrics, src=language, dest="en")
            text = translated.text
        else:
            text = lyrics

        # Sentiment Score berechnen
        blob = TextBlob(text)
        polarity = round(blob.sentiment.polarity, 4)  # -1 = negativ, +1 = positiv

        output_collection.insert_one({
            "artist": artist,
            "tag": tag,
            "language": language,
            "year": year,
            "views": views,
            "sentiment_score": polarity,
            "title": title,
        })

    except Exception as e:
        print(f"Fehler bei Song von {artist}: {e}")
        continue

print("✅ Sentimentanalyse für Songs abgeschlossen und gespeichert.")

Fehler bei Song von Emis Killa & Jake La Furia: The read operation timed out
Fehler bei Song von Real Talk: the JSON object must be str, bytes or bytearray, not NoneType
Fehler bei Song von Briga: The read operation timed out
Fehler bei Song von Kill Mauri: _ssl.c:1112: The handshake operation timed out
Fehler bei Song von DrefGold: The read operation timed out
Fehler bei Song von Frah Quintale: _ssl.c:1112: The handshake operation timed out
Fehler bei Song von Eros Ramazzotti: The read operation timed out
Fehler bei Song von Pacman XII: The read operation timed out
Fehler bei Song von MezzoSangue: The read operation timed out
Fehler bei Song von Rudy Marra: The read operation timed out
Fehler bei Song von Sinomine: The read operation timed out
Fehler bei Song von Carati Crew: the JSON object must be str, bytes or bytearray, not NoneType
Fehler bei Song von Gazzelle: The read operation timed out
Fehler bei Song von Frabolo: the JSON object must be str, bytes or bytearray, not NoneType


KeyboardInterrupt: 

In [ ]:
from pymongo import MongoClient
from textblob import TextBlob
from googletrans import Translator
import re

# Verbindung zur MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
collection = db["sampled_subset_en"]
output_collection = db["song_sentiment_analysis_en"]

translator = Translator()

# Songs laden
songs = collection.find({
    "lyrics": {"$exists": True, "$ne": None},
    "language": {"$in": ["en", "de", "es", "fr", "it"]},
    "artist": {"$exists": True},
    "tag": {"$exists": True},
    "year": {"$exists": True},
    "views": {"$exists": True}
})

output_collection.delete_many({})  # Bestehende Einträge löschen

song_number = 1

for song in songs:
    lyrics = song.get("lyrics", "")
    language = song.get("language", "en")
    artist = str(song.get("artist", "")).strip()
    tag = str(song.get("tag", "unknown")).lower()
    year = song.get("year", None)
    views = song.get("views", 0)
    title = song.get("title", "unknown")

    if not lyrics or not artist or not language:
        continue

    try:
        print(f"{song_number}. Analysiere Song: '{title}' von {artist} ({language})...")
        # Wenn die Sprache nicht Englisch ist, übersetzen
        if language != "en":
            translated = translator.translate(lyrics, src=language, dest="en")
            text = translated.text
        else:
            text = lyrics

        # Sentiment Score berechnen
        blob = TextBlob(text)
        polarity = round(blob.sentiment.polarity, 4)  # -1 = negativ, +1 = positiv

        output_collection.insert_one({
            "artist": artist,
            "tag": tag,
            "language": language,
            "year": year,
            "views": views,
            "sentiment_score": polarity,
            "title": title,
        })

        song_number += 1

    except Exception as e:
        print(f"❌ Fehler bei Song: '{title}' von {artist}: {e}")
        continue

print("✅ Sentimentanalyse für alle Songs abgeschlossen und gespeichert.")


1. Analysiere Song: 'As God Wills' von OG MOOSE (en)...
2. Analysiere Song: 'Your Soul and Mine' von Gil Scott-Heron (en)...
3. Analysiere Song: 'Get a bag jit' von Imbadkidray (en)...
4. Analysiere Song: 'LoveHate' von Kelvyn Colt (en)...
5. Analysiere Song: 'Blue Eyes Red' von Addison Johnson (en)...
6. Analysiere Song: '4 Xans' von Lil Drum (en)...
7. Analysiere Song: 'Love Begins with You' von Dionne Warwick (en)...
8. Analysiere Song: 'Just Add Water' von AZtheMC (en)...
9. Analysiere Song: 'Smile' von Lukas Nelson & Promise Of The Real (en)...
10. Analysiere Song: 'Never Run Dry' von Vineyard Worship (en)...
11. Analysiere Song: 'Portrait' von Weepgoth (en)...
12. Analysiere Song: 'The Life and Adventures of Robinson Crusoe Chap. 20' von Daniel Defoe (en)...
13. Analysiere Song: 'Pastime Paradise' von Billy Mackenzie (en)...
14. Analysiere Song: 'Hole In My Heart' von Matt Pond (en)...
15. Analysiere Song: 'Summertime' von TruthCity (en)...
16. Analysiere Song: 'Lit onna hunnid' 

In [41]:
from pymongo import MongoClient
from textblob import TextBlob
from googletrans import Translator
import re

# Verbindung zur MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]
collection = db["sampled_subset_es"]
output_collection = db["song_sentiment_analysis_es"]

translator = Translator()

# Songs laden
songs = collection.find({
    "lyrics": {"$exists": True, "$ne": None},
    "language": {"$in": ["en", "de", "es", "fr", "it"]},
    "artist": {"$exists": True},
    "tag": {"$exists": True},
    "year": {"$exists": True},
    "views": {"$exists": True}
})

output_collection.delete_many({})  # Bestehende Einträge löschen

song_number = 1

for song in songs:
    lyrics = song.get("lyrics", "")
    language = song.get("language", "en")
    artist = str(song.get("artist", "")).strip()
    tag = str(song.get("tag", "unknown")).lower()
    year = song.get("year", None)
    views = song.get("views", 0)
    title = song.get("title", "unknown")

    if not lyrics or not artist or not language:
        continue

    try:
        print(f"{song_number}. Analysiere Song: '{title}' von {artist} ({language})...")
        # Wenn die Sprache nicht Englisch ist, übersetzen
        if language != "en":
            translated = translator.translate(lyrics, src=language, dest="en")
            text = translated.text
        else:
            text = lyrics

        # Sentiment Score berechnen
        blob = TextBlob(text)
        polarity = round(blob.sentiment.polarity, 4)  # -1 = negativ, +1 = positiv

        output_collection.insert_one({
            "artist": artist,
            "tag": tag,
            "language": language,
            "year": year,
            "views": views,
            "sentiment_score": polarity,
            "title": title,
        })

        song_number += 1

    except Exception as e:
        print(f"❌ Fehler bei Song: '{title}' von {artist}: {e}")
        continue

print("✅ Sentimentanalyse für alle Songs abgeschlossen und gespeichert.")


1. Analysiere Song: 'Mi mejor regalo' von Los Primos De Durango (es)...
2. Analysiere Song: 'Corre - Jesse  Joy letra' von Jean Carlos Heigl (es)...
3. Analysiere Song: 'No Pibe' von Manal (Band) (es)...
4. Analysiere Song: 'Fuego' von Laura Guevara (es)...
5. Analysiere Song: 'Cuando tenga viento en mi cráneo' von Nacha Guevara (es)...
6. Analysiere Song: 'Ignorantes' von Bad Bunny & Sech (es)...
7. Analysiere Song: 'Chile lindo' von Los huasos quincheros (es)...
8. Analysiere Song: 'Pozo de los deseos' von Rayden (es)...
9. Analysiere Song: 'Munra o Don Draper' von Letelefono (es)...
10. Analysiere Song: 'Contamíname En Directo' von Vctor Manuel (es)...
11. Analysiere Song: 'Piel Canela' von CUCO (es)...
12. Analysiere Song: 'Viaje a los confines del universo' von Julian X's Gunvolt (es)...
13. Analysiere Song: 'Tres Xs' von Triple XXX (es)...
14. Analysiere Song: 'BDAY' von WuMo The Flame Boucher (es)...
15. Analysiere Song: 'Mundo Bicolor' von Rapsusklei & Aniki (es)...
16. Analysi

In [48]:
from pymongo import MongoClient

# Verbindung zur MongoDB
client = MongoClient("mongodb://localhost:27017")  # ggf. URL anpassen
db = client["data"]                  # Name deiner Datenbank
collection = db["song_sentiment_analysis_it"]                # Name deiner Collection

# Dokumente löschen, bei denen das Jahr kleiner als 1950 ist
result = collection.delete_many({"year": {"$lt": 1950}})

# Anzahl gelöschter Dokumente anzeigen
print(f"{result.deleted_count} Songs wurden gelöscht.")


7 Songs wurden gelöscht.


In [50]:
from pymongo import MongoClient

client = MongoClient("mongodb://localhost:27017")  # ggf. anpassen
db = client["data"]                  # <-- anpassen
collection = db["sampled_subset"]                # <-- anpassen

pipeline = [
    {
        "$group": {
            "_id": {
                "tag": "$tag",
                "language": "$language",
                "artist": "$artist"
            },
            "total_views": {"$sum": "$views"},
            "songs": {"$addToSet": "$title"}  # optional: Titel aller Songs
        }
    },
    {
        "$group": {
            "_id": {
                "tag": "$_id.tag",
                "language": "$_id.language"
            },
            "artists": {
                "$push": {
                    "artist": "$_id.artist",
                    "total_views": "$total_views",
                    "songs": "$songs"
                }
            }
        }
    },
    {
        "$project": {
            "_id": 1,
            "top_artists": {
                "$slice": [
                    {
                        "$sortArray": {
                            "input": "$artists",
                            "sortBy": {"total_views": -1}
                        }
                    },
                    10
                ]
            }
        }
    }
]

results = collection.aggregate(pipeline)

# Ausgabe formatieren
for group in results:
    tag = group["_id"]["tag"]
    lang = group["_id"]["language"]
    print(f"\n🎧 Genre: {tag} | Sprache: {lang}")
    for artist_entry in group["top_artists"]:
        print(f"- {artist_entry['artist']} ({artist_entry['total_views']} Views)")
        



🎧 Genre: country | Sprache: de
- Hank Hberle Jr. (531 Views)
- Franzi25 (247 Views)
- Larry Schuba und Western Union (107 Views)

🎧 Genre: country | Sprache: en
- Brad Paisley (365408 Views)
- Taylor Swift (266417 Views)
- Cody Jinks (237227 Views)
- Shania Twain (182949 Views)
- Florida Georgia Line (169404 Views)
- Morgan Wallen (140486 Views)
- Hank Williams (90134 Views)
- Steve Earle (83621 Views)
- Brooks & Dunn (74332 Views)
- John Prine (68551 Views)

🎧 Genre: country | Sprache: es
- Natanael Cano (18526 Views)
- C. Tangana, Carin Leon & Adriel Favela (15135 Views)
- Eslabon Armado (9668 Views)
- Jos Alfredo Jimnez (5393 Views)
- Chalino Snchez (4610 Views)
- WOW (Fictional) (3433 Views)
- Alejandro Fernndez (1401 Views)
- Natanael Cano & La Nueva Era (1001 Views)
- T3R Elemento (636 Views)
- Velvetine (633 Views)

🎧 Genre: country | Sprache: fr
- Baptiste W. Hamon (843 Views)
- Avec pas d'casque (251 Views)
- Jewel Usain (215 Views)
- Baaziz (148 Views)
- Canailles (133 Views

In [ ]:
from pymongo import MongoClient
import re

# MongoDB-Verbindung
client = MongoClient("mongodb://localhost:27017")
db = client["data"]
collection = db["sampled_subset_it"] # für jede Sprache abkürzung anpassen

# Wörter, die ignoriert werden sollen (können angepasst/erweitert werden)
ignore_words = {
    "intro", "outro", "hook", "chorus", "verse", "bridge",
    "refrain", "pre-chorus", "interlude", "instrumental",
    "part", "beat", "drop"
}

# Regex, um Lyrics zu bereinigen
def clean_lyrics(text):
    lines = text.lower().splitlines()
    cleaned = []
    for line in lines:
        line = line.strip()
        # Ignoriere Zeilen wie [Intro], (Intro), oder auch ohne Klammern
        if re.match(r'^\[?.*(' + '|'.join(ignore_words) + r').*\]?', line):
            continue
        if any(w in line for w in ignore_words):
            continue
        cleaned.append(line)
    return ' '.join(cleaned)

# Songs ohne Metriken holen
songs = collection.find({
    "lyrics": {"$exists": True, "$ne": ""},
    "$or": [
        {"avg_word_length": {"$exists": False}},
        {"vocab_richness": {"$exists": False}}
    ]
})

total = collection.count_documents({
    "lyrics": {"$exists": True, "$ne": ""},
    "$or": [
        {"avg_word_length": {"$exists": False}},
        {"vocab_richness": {"$exists": False}}
    ]
})

print(f"Berechne Metriken für {total} Songs...\n")

for i, song in enumerate(songs, 1):
    raw_lyrics = song["lyrics"]
    cleaned_lyrics = clean_lyrics(raw_lyrics)

    words = re.findall(r'\b\w+\b', cleaned_lyrics)
    if len(words) < 5:
        print(f"[{i}/{total}] Überspringe '{song.get('title', 'Unbekannt')}' – zu wenig gültige Wörter.")
        continue

    total_words = len(words)
    unique_words = len(set(words))
    avg_word_length = sum(len(w) for w in words) / total_words
    vocab_richness = unique_words / total_words

    # Dokument aktualisieren
    collection.update_one(
        {"_id": song["_id"]},
        {"$set": {
            "avg_word_length": round(avg_word_length, 3),
            "vocab_richness": round(vocab_richness, 3)
        }}
    )

    print(f"[{i}/{total}] Verarbeitet: {song.get('title', 'Unbekannt')} ({song.get('artist', '-')})")

print("\n✅ Berechnung abgeschlossen.")


Berechne Metriken für 2644 Songs...

[1/2644] Verarbeitet: Come i più grandi (3D)
[2/2644] Verarbeitet: DAFNE (Liverga)
[3/2644] Verarbeitet: 8 DICEMBRE (RATTOBOYS)
[4/2644] Verarbeitet: Cavalli Di Troia (Wing Klan)
[5/2644] Verarbeitet: Nuovo Canada (Capo Plaza)
[6/2644] Verarbeitet: Sogno (Paul Schwartz)
[7/2644] Verarbeitet: Con le tasche leggere (Coez)
[8/2644] Verarbeitet: Io (Vale Lambo)
[9/2644] Verarbeitet: Lartista (Nicola Di Bari)
[10/2644] Verarbeitet: Ancora Un Po Di Più (Marina Perzy)
[11/2644] Verarbeitet: Boccadasse (Ornella Vanoni)
[12/2644] Verarbeitet: D-A-MANTI-D (Xni)
[13/2644] Verarbeitet: Devil May Cry (Golhetti)
[14/2644] Verarbeitet: Quello che non ho (Emis Killa & Jake La Furia)
[15/2644] Verarbeitet: Real Talk - Pepito Rella x Remmy x Egreen (Real Talk)
[16/2644] Verarbeitet: Stories Di Tutti i Giorni (Macro Marco & Don Diegoh)
[17/2644] Verarbeitet: Nodi In Gola (XVI Religion)
[18/2644] Verarbeitet: Ci Rivedo Te (Divo Scarfake)
[19/2644] Verarbeitet: Enrico I

In [ ]:
from pymongo import MongoClient
import re

# MongoDB-Verbindung
client = MongoClient("mongodb://localhost:27017/")
db = client["data"]  # <-- anpassen
collection = db["sampled_subset_it"]  # für jede Sprache abkürzung anpassen

# Liste mit Keywords, die ignoriert werden sollen
IGNORED_SECTIONS = [
    r'\[?\s*intro\s*\]?', r'\[?\s*outro\s*\]?', r'\[?\s*bridge\s*\]?',
    r'\[?\s*hook\s*\]?', r'\[?\s*chorus\s*\]?', r'\[?\s*refrain\s*\]?',
    r'\[?\s*verse\s*\d*\]?', r'\[?\s*pre[- ]?chorus\s*\]?', r'\[?\s*interlude\s*\]?', r'\[?\s*part\s*\d*\]?'
]

# Regex-Muster zum Entfernen ganzer Zeilen mit solchen Abschnitten
ignored_pattern = re.compile(r'^(' + '|'.join(IGNORED_SECTIONS) + r')\s*$', flags=re.IGNORECASE | re.MULTILINE)

# Alle Songs laden
songs = list(collection.find({'lyrics': {'$exists': True}}))
total = len(songs)

for i, song in enumerate(songs, 1):
    raw_lyrics = song.get("lyrics", "").strip()

    print(f"[{i}/{total}] {song.get('title', 'Unbekannt')}")

    # Entferne alle Zeilen, die nur einen dieser Marker enthalten
    cleaned_lyrics = ignored_pattern.sub('', raw_lyrics)

    # Entferne ggf. doppelte Leerzeilen
    cleaned_lyrics = re.sub(r'\n{2,}', '\n', cleaned_lyrics).strip()

    # Wortanzahl zählen
    word_count = len(cleaned_lyrics.split())

    # In der Datenbank speichern
    collection.update_one(
        {'_id': song['_id']},
        {'$set': {'lyrics_word_count': word_count}}
    )


[1/2644] Come i più grandi
[2/2644] DAFNE
[3/2644] 8 DICEMBRE
[4/2644] Cavalli Di Troia
[5/2644] Nuovo Canada
[6/2644] Sogno
[7/2644] Con le tasche leggere
[8/2644] Io
[9/2644] Lartista
[10/2644] Ancora Un Po Di Più
[11/2644] Boccadasse
[12/2644] D-A-MANTI-D
[13/2644] Devil May Cry
[14/2644] Quello che non ho
[15/2644] Real Talk - Pepito Rella x Remmy x Egreen
[16/2644] Stories Di Tutti i Giorni
[17/2644] Nodi In Gola
[18/2644] Ci Rivedo Te
[19/2644] Enrico IV
[20/2644] Sei Tu
[21/2644] Nessuna Pietà
[22/2644] La mia testa prima di me Variazione sul tema ”Prima fila Mississipi”
[23/2644] Stronza RMX
[24/2644] La Cao Di Fine Del Mondo
[25/2644] Nitrisce
[26/2644] Intro
[27/2644] Mino - Ribadisco Bar
[28/2644] Tu Te Scurdat E Me Illegal RMX
[29/2644] Caramella
[30/2644] Adorando La Bestia
[31/2644] Comincia lo show
[32/2644] BOOMERS
[33/2644] La casa nel parco
[34/2644] Gli ostacoli del cuore
[35/2644] Il corrotto
[36/2644] Azzurri Nel Blu
[37/2644] Tutto o Niente
[38/2644] 105 Mi Casa M